In [ ]:
%matplotlib inline


# Robustness

In this example, we illustrate the use of the :class:`.Robustness` plot
on the Sobieski's SSBJ problem.


In [ ]:
from __future__ import division, unicode_literals

from matplotlib import pyplot as plt

## Import
The first step is to import some functions from the API
and a method to get the design space.



In [ ]:
from gemseo.api import configure_logger, create_discipline, create_scenario
from gemseo.problems.sobieski.core import SobieskiProblem

configure_logger()

## Description

In the :class:`~gemseo.post.robustness.Robustness` post-processing,
the robustness of the optimum is represented by a box plot. Using the
quadratic approximations of all the output functions, we
propagate analytically a normal distribution with 1% standard deviation
on all the design variables, assuming no cross-correlations of inputs,
to obtain the mean and standard deviation of the resulting normal
distribution. A series of samples are randomly generated from the resulting
distribution, whose quartiles are plotted, relatively to the values of
the function at the optimum. For each function (in abscissa), the plot
shows the extreme values encountered in the samples (top and bottom
bars). Then, 95% of the values are within the blue boxes. The average is
given by the red bar.



## Create disciplines
At this point, we instantiate the disciplines of Sobieski's SSBJ problem:
Propulsion, Aerodynamics, Structure and Mission



In [ ]:
disciplines = create_discipline(
    [
        "SobieskiPropulsion",
        "SobieskiAerodynamics",
        "SobieskiStructure",
        "SobieskiMission",
    ]
)

## Create design space
We also read the design space from the :class:`.SobieskiProblem`.



In [ ]:
design_space = SobieskiProblem().read_design_space()

## Create and execute scenario
The next step is to build an MDO scenario in order to maximize the range,
encoded 'y_4', with respect to the design parameters, while satisfying the
inequality constraints 'g_1', 'g_2' and 'g_3'. We can use the MDF formulation,
the SLSQP optimization algorithm
and a maximum number of iterations equal to 100.



In [ ]:
scenario = create_scenario(
    disciplines,
    formulation="MDF",
    objective_name="y_4",
    maximize_objective=True,
    design_space=design_space,
)
scenario.set_differentiation_method("user")
for constraint in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(constraint, "ineq")
scenario.execute({"algo": "SLSQP", "max_iter": 10})

## Post-process scenario
Lastly, we post-process the scenario by means of the :class:`.Robustness`
which plots any of the constraint or
objective functions w.r.t. the optimization iterations or sampling snapshots.



.. tip::

   Each post-processing method requires different inputs and offers a variety
   of customization options. Use the API function
   :meth:`~gemseo.api.get_post_processing_options_schema` to print a table with
   the options for any post-processing algorithm.
   Or refer to our dedicated page:
   `gen_post_algos`.



In [ ]:
scenario.post_process("Robustness", save=False, show=False)
# Workaround for HTML rendering, instead of ``show=True``
plt.show()